In [2]:
import pandas as pd
import torch
import os
import numpy as np
import helpers
from datasets import Dataset
from transformers import BertConfig, BertTokenizerFast,  BertForSequenceClassification,  PreTrainedTokenizerFast
from tokenizers import decoders, models, normalizers, pre_tokenizers, processors, trainers, Tokenizer

In [3]:
import importlib
importlib.reload(helpers)

<module 'helpers' from '/lustre/isaac/scratch/ababjac/codon-sentiment-score/bert-scripts/helpers.py'>

In [4]:
PATH='/lustre/isaac/proj/UTK0196/codon-expression-data/fullTableForTrainning/'

In [5]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu') # Tells the model we need to use the GPU

In [6]:
filelist = os.listdir(PATH) 
df_list = [pd.read_csv(PATH+file) for file in filelist]
df = pd.concat(df_list)

In [7]:
df

GeneName  median_exp                                           Sequence
0       Gnai3       35.00  ATGGGCTGCACGTTGAGCGCCGAGGACAAGGCGGCGGTGGAGCGGA...
1       Cdc45        1.45  ATGTTCGTGACCGATTTCCGCAAGGAGTTCTACGAGACGGTCCACA...
2       Scml2        1.00  ATGGCAGAGCCTGCCACTGGAGTGCAACTTGCTGGTTCTGGAGAGC...
3        Apoh        0.10  ATGGTTTCCCCGGTGCTCGCCTTGTTCTCCGCCTTCCTCTGCCATG...
4        Narf       10.00  ATGAAGTGTGAGCACTGCACACGAAAGGAATGTAGTAAAAAATCAA...
...       ...         ...                                                ...
5031     OPT2        8.00  ATGAGTGAAACAGTCAAAGATAAAGTTATAATTGATGAGAAGGTAT...
5032     SGE1       60.00  ATGAAGAGTACTTTGAGTTTAACTTTATGTGTTATATCGCTTCTAT...
5033     ARR1       39.00  ATGGCAAAACCGCGTGGAAGAAAAGGCGGCAGGAAGCCTTCACTTA...
5034     ARR2       13.00  ATGGTAAGTTTCATAACGTCTAGGCAACTCAAGGGCCTAATTGAAA...
5035     ARR3       10.00  ATGTCAGAAGATCAAAAAAGTGAAAATTCGGTACCTTCTAAGGTTA...

[71820 rows x 3 columns]

In [8]:
df = helpers.add_codons_to_df(df, 'Sequence')
labels = np.where(df['median_exp'] > np.median(df['median_exp'].values), 1, 0)

classification_df = pd.DataFrame({'text' : df['codons_cleaned'], 'label' : labels})

/lustre/isaac/scratch/ababjac/codon-sentiment-score/bert-scripts/helpers.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['codons_cleaned'] = get_codon_list(df[col])


In [9]:
MAX = int(np.median([(len(elem) / 3) for elem in df['codons_cleaned']]))
MAX

502

In [10]:
def compute_metrics(epred):
    # Computes metrics from specialized output from huggingface

    preds = np.exp(epred[0]) / np.sum(np.exp(epred[0]), axis = 0)
    labels = epred[1]

    metrics = {}
    metrics['auprc'] = average_precision_score(labels, preds[:,1])
    metrics['auroc'] = roc_auc_score(labels, preds[:,1])

    return metrics

In [11]:
ds = Dataset.from_pandas(classification_df)

In [12]:
tokenizer = Tokenizer(models.WordPiece(unk_token="[UNK]"))

In [13]:
tokenizer.normalizer = normalizers.BertNormalizer(lowercase=True)

In [14]:
tokenizer.pre_tokenizer = pre_tokenizers.BertPreTokenizer()

In [15]:
tokenizer.mask_token="[MASK]"

In [16]:
special_tokens = ["[UNK]", "[PAD]", "[CLS]", "[SEP]", "[MASK]"]

In [17]:
trainer = trainers.WordPieceTrainer(special_tokens=special_tokens)

In [18]:
batch_size = 1000
all_texts = [ds[i : i + batch_size]['text'] for i in range(0, len(ds), batch_size)]

def batch_iterator():
    for i in range(0, len(ds), batch_size):
        yield ds[i : i + batch_size]['text']

In [19]:
tokenizer.train_from_iterator(batch_iterator(), trainer=trainer)

In [20]:
fast_tokenizer = BertTokenizerFast(tokenizer_object=tokenizer)

In [21]:
fast_tokenizer.mask_token='[MASK]'
fast_tokenizer.pad_token='[PAD]'
fast_tokenizer.cls_token='[CLS]'
fast_tokenizer.unk_token='[UNK]'

In [22]:
fast_tokenizer.save_pretrained('../tokenizers/codonBERT')

('../tokenizers/codonBERT/tokenizer_config.json',
 '../tokenizers/codonBERT/special_tokens_map.json',
 '../tokenizers/codonBERT/vocab.txt',
 '../tokenizers/codonBERT/added_tokens.json',
 '../tokenizers/codonBERT/tokenizer.json')

In [23]:
#testing it
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained('../tokenizers/codonBERT')

In [26]:
tokenized_ds = ds.map(lambda d : tokenizer(d['text'], truncation=True, padding=True, max_length=512), batched=True)

Map:   0%|          | 0/70741 [00:00<?, ? examples/s]

In [28]:
tokenized_ds['attention_mask']

[[1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
